# Convert Series to Rates per 100,000

In [1]:
import pandas as pd
import os

In [2]:
ts_folder = "../data/covid-19_jhu-csse/"
wb_path = "../data/worldbank/SP.POP.TOTL.zip"
out_folder = None
PAPERMILL_OUTPUT_PATH = None

In [3]:
# Parameters
PAPERMILL_INPUT_PATH = "/tmp/hmyw2rom/notebooks/ToRates.ipynb"
PAPERMILL_OUTPUT_PATH = "runs/ToRates.run.ipynb"
ts_folder = "/tmp/hmyw2rom/data/covid-19_jhu-csse"
wb_path = "/tmp/hmyw2rom/data/worldbank/SP.POP.TOTL.zip"
out_folder = "data/covid-19_rates"


## Read in JHU CSSE data

I will switch to [xarray](http://xarray.pydata.org/en/stable/), but ATM, it's easier like this...

In [4]:
def read_jhu_covid_region_df(name):
    filename = os.path.join(ts_folder, f"time_series_19-covid-{name}.csv")
    df = pd.read_csv(filename)
    df = df.set_index(['Country/Region', 'Province/State', 'Lat', 'Long'])
    df.columns = pd.to_datetime(df.columns)
    region_df = df.groupby(level='Country/Region').sum()
    loc_df = df.reset_index([2,3]).groupby(level='Country/Region').mean()[['Long', 'Lat']]
    return region_df.join(loc_df).set_index(['Long', 'Lat'], append=True)

In [5]:
frames_map = {
    "confirmed": read_jhu_covid_region_df("Confirmed"),
    "deaths": read_jhu_covid_region_df("Deaths"),
    "recovered": read_jhu_covid_region_df("Recovered")
}

In [6]:
frames_map['confirmed'].sort_values(frames_map['confirmed'].columns[-1], ascending=False).head()

2020-01-22  2020-01-23  2020-01-24  \
Country/Region Long        Lat                                             
China           111.649082 32.828385         548         643         920   
Italy           12.000000  43.000000           0           0           0   
Iran            53.000000  32.000000           0           0           0   
Korea, South    128.000000 36.000000           1           1           2   
France         -41.223233  27.399467           0           0           2   

                                      2020-01-25  2020-01-26  2020-01-27  \
Country/Region Long        Lat                                             
China           111.649082 32.828385        1406        2075        2877   
Italy           12.000000  43.000000           0           0           0   
Iran            53.000000  32.000000           0           0           0   
Korea, South    128.000000 36.000000           2           3           4   
France         -41.223233  27.399467           3           3           3   

                                      2020-01-28  2020-01-29  2020-01-30  \
Country/Region Long        Lat                                             
China           111.649082 32.828385        5509        6087        8141   
Italy           12.000000  43.000000           0           0           0   
Iran            53.000000  32.000000           0           0           0   
Korea, South    128.000000 36.000000           4           4           4   
France         -41.223233  27.399467           4           5           5   

                                      2020-01-31  ...  2020-03-03  2020-03-04  \
Country/Region Long        Lat                    ...                           
China           111.649082 32.828385        9802  ...       80261       80386   
Italy           12.000000  43.000000           2  ...        2502        3089   
Iran            53.000000  32.000000           0  ...        2336        2922   
Korea, South    128.000000 36.000000          11  ...        5186        5621   
France         -41.223233  27.399467           5  ...         204         288   

                                      2020-03-05  2020-03-06  2020-03-07  \
Country/Region Long        Lat                                             
China           111.649082 32.828385       80537       80690       80770   
Italy           12.000000  43.000000        3858        4636        5883   
Iran            53.000000  32.000000        3513        4747        5823   
Korea, South    128.000000 36.000000        6088        6593        7041   
France         -41.223233  27.399467         380         656         952   

                                      2020-03-08  2020-03-09  2020-03-10  \
Country/Region Long        Lat                                             
China           111.649082 32.828385       80823       80860       80887   
Italy           12.000000  43.000000        7375        9172       10149   
Iran            53.000000  32.000000        6566        7161        8042   
Korea, South    128.000000 36.000000        7314        7478        7513   
France         -41.223233  27.399467        1129        1212        1787   

                                      2020-03-11  2020-03-12  
Country/Region Long        Lat                                
China           111.649082 32.828385       80921       80932  
Italy           12.000000  43.000000       12462       12462  
Iran            53.000000  32.000000        9000       10075  
Korea, South    128.000000 36.000000        7755        7869  
France         -41.223233  27.399467        2284        2284  

[5 rows x 51 columns]

# Read in World Bank data

In [7]:
import zipfile
zf = zipfile.ZipFile(wb_path)
pop_df = pd.read_csv(zf.open("API_SP.POP.TOTL_DS2_en_csv_v2_821007.csv"), skiprows=4)

There is 2018 pop data for all countries/regions except Eritrea

In [8]:
pop_df[pd.isna(pop_df['2018'])]

Country Name Country Code     Indicator Name Indicator Code       1960  \
67          Eritrea          ERI  Population, total    SP.POP.TOTL  1007590.0   
108  Not classified          INX  Population, total    SP.POP.TOTL        NaN   

          1961       1962       1963       1964       1965  ...       2011  \
67   1033328.0  1060486.0  1088854.0  1118159.0  1148189.0  ...  3213972.0   
108        NaN        NaN        NaN        NaN        NaN  ...        NaN   

     2012  2013  2014  2015  2016  2017  2018  2019  Unnamed: 64  
67    NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN          NaN  
108   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN          NaN  

[2 rows x 65 columns]

Fix the country/region names that differ between the World Bank population data and the JHU CSSE data.

In [9]:
region_wb_jhu_map = {
    'China': 'Mainland China',
     'Iran, Islamic Rep.': 'Iran (Islamic Republic of)',
     'Korea, Rep.': 'Republic of Korea',
     'United States': 'US',
     'United Kingdom': 'UK',
     'Hong Kong SAR, China': 'Hong Kong SAR',
     'Egypt, Arab Rep.': 'Egypt',
     'Vietnam': 'Viet Nam',
     'Macao SAR, China': 'Macao SAR',
     'Slovak Republic': 'Slovakia',
     'Moldova': 'Republic of Moldova',
     'St. Martin (French part)': 'Saint Martin',
     'Brunei Darussalam': 'Brunei'
}
current_pop_ser = pop_df[['Country Name', '2018']].copy().replace(region_wb_jhu_map).set_index('Country Name')['2018']
data_pop_ser = current_pop_ser[current_pop_ser.index.isin(frames_map['confirmed'].index.levels[0])]

There are some regions that we cannot resolve, but we will just ignore these.

# Compute rates per 100,000 for regions

In [10]:
def cases_to_rates_df(df):
    per_100000_df = df.reset_index([1, 2], drop=True)
    per_100000_df = per_100000_df.div(data_pop_ser, 'index').mul(100000).dropna()
    per_100000_df.index.name = 'Country/Region'
    return per_100000_df
    
def frames_to_rates(frames_map):
    return {k: cases_to_rates_df(v) for k,v in frames_map.items()}


rates_map = frames_to_rates(frames_map)

In [11]:
if PAPERMILL_OUTPUT_PATH:
    for k, v in rates_map.items():
        out_path = os.path.join(out_folder, f"ts_rates_19-covid-{k}.csv")
        v.reset_index().to_csv(out_path)